In [2]:
#1. load skybox image of the path[-3:]
#2. display instruction, adversarial instruction, (navgpt captions and objects)

from PIL import Image
import json, os

def load_json(fn):
    with open(fn) as f:
        ret = json.load(f)
    return ret

def dump_json(data, fn, force=False):
    if not force:
        assert not os.path.exists(fn)
    with open(fn, 'w') as f:
        json.dump(data, f)
        
def concat_images(images):
    #images = [Image.open(x) for x in ['Test1.jpg', 'Test2.jpg', 'Test3.jpg']]
    widths, heights = zip(*(i.size for i in images))

    total_width = sum(widths)+(len(images)-1)*10
    max_height = max(heights)

    new_im = Image.new('RGB', (total_width, max_height))

    x_offset = 0
    for im in images:
        new_im.paste(im, (x_offset,0))
        x_offset += im.size[0]+10
    return new_im

In [4]:
reverie_val_unseen = load_json('../REVERIE/tasks/REVERIE/data/REVERIE_val_unseen_first_ins.json')
reverie_val_unseen_fnf = load_json("..//fnf/reverie_val_unseen_fnf.json")

In [10]:
fnf_pairs = []
for idx, r in enumerate(reverie_val_unseen_fnf):
    if not r['found']:
        fnf_pairs.append((reverie_val_unseen_fnf[idx-1], r))

In [25]:
idx = 1
fnf_pair = fnf_pairs[idx]

In [ ]:
scan_id, path = fnf_pair[0]['scan'], fnf_pair[0]['path']
fn_template = '/work/ganymede9487/mp3d/unzipped/{}/matterport_skybox_images/{}_skybox{}_sami.jpg'
skybox_image_files = [fn_template.format(scan_id, path[-1], skybox_idx) for skybox_idx in range(6)]
skybox_images = []
for skybox_image_file in skybox_image_files:
    skybox_images.append(Image.open(skybox_image_file))

concat_images(skybox_images)




In [27]:
print(fnf_pair[0]['instruction'])
print(fnf_pair[1]['instruction'])

Go to the lounge on level 1 with the fire extinguisher and push the rope around the table closer to the walls
Go to the lounge on level 1 with the fire extinguisher and push the towel around the table closer to the walls


In [ ]:
#0 ok
#1 error 2 (not reasonable)

In [ ]:
# Visualizer
# data loader part
from PIL import Image
import networkx as nx
import json
import os
import matplotlib.pyplot as plt
from matplotlib.patches import Rectangle
from io import BytesIO
import IPython.display

# ================================== DATA DOWNLOAD ==================================
#
# DATASET: default to "val unseen"
# IMG_DIR_PATH: where to store the skyboxes images
    # which the Matterport Sim used.
# ANNOTATION_DIR_PATH: where to store the "adversarial instruction ver" annotations
    # download here: https://snsd0805.com/data/adversarial_annotations.zip
# PREDICTS_PATH: predict output (download here (duet version): )
    # download here(duet's prediction): https://snsd0805.com/data/submit_val_unseen_dynamic.json
# CONNECTIVITY_PATH: where to store the connectivity file
    # download here (provided by NavGPT): https://www.dropbox.com/sh/i8ng3iq5kpa68nu/AAB53bvCFY_ihYx1mkLlOB-ea?dl=1
# NAVIGABLE_PATH: 
    # the download link is same as CONNECTIVITY_PATH's
# BBOXES_FILE_PATH: 
    # download here: https://snsd0805.com/data/BBoxes.json
#
# ===================================================================================
DATASET = "val_unseen"
IMG_DIR_PATH = "/home/snsd0805/code/research/VLN/base_dir/v1/scans"
ANNOTATION_DIR_PATH = f"/data/Matterport3DSimulator-duet/VLN-DUET/datasets/REVERIE/annotations/REVERIE_{DATASET}.json"
PREDICTS_PATH = f"/data/Matterport3DSimulator-duet/VLN-DUET/datasets/REVERIE/exprs_map/finetune/dagger-vitbase-seed.0/preds/submit_{DATASET}_dynamic.json"
CONNECTIVITY_PATH = "/data/Matterport3DSimulator-duet/connectivity"
NAVIGABLE_PATH = "/data/NavGPT_data/navigable"
BBOXES_FILE_PATH = "/data/Matterport3DSimulator-duet/VLN-DUET/datasets/REVERIE/annotations/BBoxes.json"

def load_predicts() -> dict:
    with open(PREDICTS_PATH) as fp:
        data = json.load(fp)
    return data

def load_annotations() -> dict:
    with open(ANNOTATION_DIR_PATH) as fp:
        origin_data = json.load(fp)
    data = {}
    for item in origin_data:
        data[item['id']] = item
    return data

def get_annotation(annotations: dict, adversarial_instr_id: str) -> dict:
    origin_instr_id, index = adversarial_instr_id[:-2], int(adversarial_instr_id[-1])
    
    ans = annotations[origin_instr_id]
    if 'instructions_l' in ans:
        del ans['instructions_l']
    ans['original_instruction'] = ans['instructions'][0]
    ans['instructions'] = ans['instructions'][index]
    ans['found'] = ans['found'][index]

    return ans

def load_scan_viewpoints():
    '''
        get all scan's viewpoints.
    '''
    scans_viewpoints = {}
    
    # load scan list
    with open(f'{CONNECTIVITY_PATH}/scans.txt') as fp:
        scans = [ scan.replace('\n', '') for scan in fp.readlines() ]
    
    
    # load all viewpoints from scan list
    for scan in scans:
        with open(f'{CONNECTIVITY_PATH}/{scan}_connectivity.json') as fp:
            data = json.load(fp)
        
        # load navigable list
        with open(f'{NAVIGABLE_PATH}/{scan}_navigable.json') as fp:
            navigable_viewpoints = json.load(fp)
                
        # save all viewpoint in the scan
        viewpoints = []
        for viewpoint in data:
            if viewpoint['included']:
                viewpoints.append({
                    'viewpoint': viewpoint['image_id'],
                    'location': {
                        'x': viewpoint['pose'][3],
                        'y': viewpoint['pose'][7],
                        'z': viewpoint['pose'][11],
                    },
                    'navigable_viewpoints': list(navigable_viewpoints[viewpoint['image_id']].keys())
                })
        scans_viewpoints[scan] = viewpoints
    return scans_viewpoints

def get_viewpoints(scans_viewpoints: dict, scan: str) -> list:
    return scans_viewpoints[scan]

def load_bboxes_data() -> dict:
    with open(BBOXES_FILE_PATH) as fp:
        data = json.load(fp)
    return data

In [ ]:
# plot trajactory part

def plot_all_scan_viewpoints(viewpoints: list, plot: bool=True):
    nodes, edges = [], []
    G = nx.Graph()
    positions = {}

    for viewpoint in viewpoints:
        x, y = viewpoint['location']['x'], viewpoint['location']['y']
        viewpoint_id = viewpoint['viewpoint']
        G.add_node(viewpoint_id)
        positions[viewpoint_id] = (x, y)
        for neighbor in viewpoint['navigable_viewpoints']:
            G.add_edge(viewpoint_id, neighbor)
    if plot:
        nx.draw(G, positions, node_size=50)
        plt.show()        
    else:
        return G, positions

    
    
    
# overview
def plot_trajs_overview(viewpoints: list, gt_anno: dict, predict: dict):
    G, positions = plot_all_scan_viewpoints(viewpoints, plot=False)
    
    edge_colors = [ 'black' for _ in G.edges ]

    max_x, max_y = -100, -100
    min_x, min_y = 100, 100

    
    # GT path
    previous_node_name = None
    for node_name in gt_anno['path']:
        pos = positions[node_name]
        max_x = max(max_x, pos[0])
        max_y = max(max_y, pos[1])
        min_x = min(min_x, pos[0])
        min_y = min(min_y, pos[1])

        if previous_node_name != None:
            for index, edge in enumerate(G.edges):
                if edge == (previous_node_name, node_name) or edge == (node_name, previous_node_name):
                    edge_colors[index] = 'red'
        previous_node_name = node_name
    
    # Predicted Path
    previous_node_name = None
    for node_name in predict['trajectory']:
        node_name = node_name[0]
        pos = positions[node_name]
        max_x = max(max_x, pos[0])
        max_y = max(max_y, pos[1])
        min_x = min(min_x, pos[0])
        min_y = min(min_y, pos[1])

        if previous_node_name != None:
            for index, edge in enumerate(G.edges):
                if edge == (previous_node_name, node_name) or edge == (node_name, previous_node_name):
                    if edge_colors[index] == 'red':
                        edge_colors[index] = 'orange'
                    else:
                        edge_colors[index] = 'blue'
        previous_node_name = node_name

    current_axis = plt.gca()
    current_axis.add_patch(Rectangle((min_x, min_y), max_x-min_x, max_y-min_y, fill=None, edgecolor='red', linewidth=0.3))

    
    nx.draw(G, positions, node_size=20, edge_color=edge_colors)
    plt.show()
    
    
    
    
# local traj
def plot_trajs_local(viewpoints: list, gt_anno: dict, predict: dict):
    def get_viewpoints_dict(viewpoints) -> dict:
        ans = {}
        for viewpoint in viewpoints:
            viewpoint_id = viewpoint['viewpoint']
            ans[viewpoint_id] = viewpoint
        return ans

    # list to dict, to find position
    viewpoints = get_viewpoints_dict(viewpoints)

    # GT traj path
    G = nx.Graph()
    positions = {}
    edge_colors = {}
    previous_node_name = None
    
    # GT path
    for index, node_name in enumerate(gt_anno['path']):
        # new node
        G.add_node(node_name)

        # find node's position
        viewpoint = viewpoints[node_name]
        x, y = viewpoint['location']['x'], viewpoint['location']['y']
        positions[node_name] = (x, y)
        
        # path edge
        if previous_node_name != None:           # not start
            G.add_edge(previous_node_name, node_name)
            edge_colors[f'{previous_node_name}_{node_name}'] = 'red'
        previous_node_name = node_name
        
        plt.text(x-0.2, y, f'{index}', fontsize=15, color='red', ha='center', va='center')

        if node_name == gt_anno['path'][0]:
            plt.text(x, y, 'START', fontsize=12, color='darkred', ha='center', va='center')
        if node_name == gt_anno['path'][-1]:
            plt.text(x, y, 'STOP', fontsize=12, color='darkred', ha='center', va='center')
        
        
    # Predicted path
    previous_node_name = None
    for node_index, node_name in enumerate(predict['trajectory']):
        node_name = node_name[0]
        # new node
        
        G.add_node(node_name)

        # find node's position
        viewpoint = viewpoints[node_name]
        x, y = viewpoint['location']['x'], viewpoint['location']['y']
        positions[node_name] = (x, y)
        
        plt.text(x+0.2, y, f'{node_index}', fontsize=15, color='blue', ha='center', va='center')
        
        # path edge
        if previous_node_name != None:           # not start
            find = False
            for index, edge in enumerate(G.edges):
                if edge == (previous_node_name, node_name) or edge == (node_name, previous_node_name):
                    if f'{previous_node_name}_{node_name}' in edge_colors:
                        if edge_colors[f'{previous_node_name}_{node_name}'] == 'red':
                            edge_colors[f'{previous_node_name}_{node_name}'] = 'orange'
                        else:
                            edge_colors[f'{previous_node_name}_{node_name}'] = 'darkblue'
                    else:
                        if edge_colors[f'{node_name}_{previous_node_name}'] == 'red':
                            edge_colors[f'{node_name}_{previous_node_name}'] = 'orange'
                        else:
                            edge_colors[f'{node_name}_{previous_node_name}'] = 'darkblue'
                    find = True
                    break
            if not find:
                G.add_edge(previous_node_name, node_name)
                edge_colors[f'{previous_node_name}_{node_name}'] = 'blue'
        previous_node_name = node_name
    
    # edge colors
    colors = []
    for edge in G.edges:
        if f'{edge[0]}_{edge[1]}' in edge_colors:
            colors.append(edge_colors[f'{edge[0]}_{edge[1]}'])
        else:
            colors.append(edge_colors[f'{edge[1]}_{edge[0]}'])
    # STOP & START label
    start, stop = predict['trajectory'][0][0], predict['trajectory'][-1][0]
    x, y = viewpoints[start]['location']['x'], viewpoints[start]['location']['y']
    plt.text(x, y, 'START', fontsize=12, color='darkblue', ha='center', va='center')
    x, y = viewpoints[stop]['location']['x'], viewpoints[stop]['location']['y']
    plt.text(x, y, 'STOP', fontsize=12, color='darkblue', ha='center', va='center')

    nx.draw(G, positions, node_size=20, edge_color=colors, with_labels=False)
    plt.show()



def plot_trajs(viewpoints: list, gt_anno: dict, predict: dict, overview: bool):
    if overview:
        plot_trajs_overview(viewpoints, gt_anno, predict)
    else:
        plot_trajs_local(viewpoints, gt_anno, predict)


In [ ]:
# skybox part
def concat_images(images):
    #images = [Image.open(x) for x in ['Test1.jpg', 'Test2.jpg', 'Test3.jpg']]
    widths, heights = zip(*(i.size for i in images))

    total_width = sum(widths)+(len(images)-1)*10
    max_height = max(heights)

    new_im = Image.new('RGB', (total_width, max_height))

    x_offset = 0
    for im in images:
        new_im.paste(im, (x_offset,0))
        x_offset += im.size[0]+10
    return new_im

def get_skyboxes(scan: str, viewpoint: list) -> list:
    ans = []
    path = f"{IMG_DIR_PATH}/{scan}/matterport_skybox_images"
    for i in range(6):
        ans.append(Image.open(f'{path}/{viewpoint}_skybox{i}_sami.jpg', 'r'))
    return ans

def get_pano(scan: str, viewpoint: dict) -> Image:
    pano = concat_images(get_skyboxes(scan, viewpoint))
    pano = pano.resize([pano.size[0]//4, pano.size[1]//4])
    return pano

def display_img(im):
    bio = BytesIO()
    im.save(bio, format='png')
    display(IPython.display.Image(bio.getvalue(), format='png'))

def get_obj_name(bboxes_data: dict, scan: str, node: str, obj_id: str):
    return bboxes_data[f'{scan}_{node}'][str(obj_id)]['name']
    
def plot_gt_panos(scan: str, traj: list, bboxes_data: dict, obj_id: str):
    for index, node in enumerate(traj):
        print(f"GT path ({index}): {node}")
        pano = get_pano(scan, node)
        display_img(pano)
        if index == len(traj)-1:
            try:
                obj_name = get_obj_name(bboxes_data, scan, node, obj_id)
                print(f"GT object: {obj_name}({obj_id})")
            except:
                print("KEY ERROR", scan, node, obj_id)
    
def plot_predict_panos(scan: str, traj: list, bboxes_data: dict, obj_id: str):
    for index, node in enumerate(traj):
        node = node[0]
        print(f"Predict path ({index}): {node}")
        pano = get_pano(scan, node)
        display_img(pano)
        if index == len(traj)-1:
            if obj_id != -1:
                try:
                    obj_name = get_obj_name(bboxes_data, scan, node, obj_id)
                    print(f"Predict object: {obj_name}({obj_id})")
                except:
                    print("KEY ERROR", scan, node, obj_id)

            else:
                print(f"Predict object: NOT_FOUND")

In [ ]:
# main 

annotations = load_annotations()
predicts = load_predicts()
scans_viewpoints = load_scan_viewpoints()
bboxes_data = load_bboxes_data()

NUMBER = 3
success = 0
for i in range(NUMBER):
    predict = predicts[i]
    annotation = get_annotation(annotations, predict['instr_id'])
    viewpoints = get_viewpoints(scans_viewpoints, annotation['scan'])
    if annotation['found'] == predict['found']:
        success += 1
    print(i)
    print(predict['instr_id'])
    print(annotation['scan'])
    print()
    print(annotation['instructions'])
    if annotation['found'] == False:
        print("Original: ", annotation['original_instruction'])
    print()
    print("GT found: ", predict['gt_found'], annotation['found'])
    print("predict found: ", predict['found'])
    print("===")
    print("target    object ID: ", annotation['objId'])
    print("predicted object ID: ", predict['pred_objid'])
#     print(annotation.keys())
#     print(predict.keys())
#     plot_all_scan_viewpoints(viewpoints)
    plot_trajs(viewpoints, annotation, predict, overview=True)
    plot_trajs(viewpoints, annotation, predict, overview=False)
    
    plot_gt_panos(annotation['scan'], annotation['path'], bboxes_data, obj_id=annotation['objId'])
    print("* " * 30)
    plot_predict_panos(annotation['scan'], predict['trajectory'], bboxes_data, obj_id=predict['pred_objid'])
    print("="*100)
    # print(ans)
#     print(viewpoints)
print(success/NUMBER)